#Project 1 Machine Learning Pipeline - Kelas Mlops Mahir

Nama : Adha Syah Majid

Dataset : complaints_sample.csv

Sumber : Kaggle

Link Dataset : https://www.kaggle.com/datasets/mohammadripan/complaint-sample

##Dataset Summary

This is a dataset of containing 20000 dataset and 19622 unique values.


##Download dataset from Kaggle

In [1]:
# install kaggle package
!pip install -q kaggle

In [2]:
# upload kaggle.json
from google.colab import files
files.upload()

Saving kaggle (1).json to kaggle (1).json


{'kaggle (1).json': b'{"username":"adhasyahmajid","key":"7c3c6c4a13f5c95e5ac34008c995a737"}'}

In [3]:
# make directory and change permission
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json
!ls ~/.kaggle

kaggle.json


In [5]:
# test kaggle dataset list
!kaggle datasets list

ref                                                                  title                                             size  lastUpdated          downloadCount  voteCount  usabilityRating  
-------------------------------------------------------------------  -----------------------------------------------  -----  -------------------  -------------  ---------  ---------------  
teocalvo/teomewhy-loyalty-system                                     TeoMeWhy Loyalty System                           22MB  2024-06-13 13:00:23             60        332  1.0              
shreyanshverma27/online-sales-dataset-popular-marketplace-data       Online Sales Dataset - Popular Marketplace Data    7KB  2024-05-25 23:55:26           6675        125  1.0              
muhammadroshaanriaz/e-commerce-trends-a-guide-to-leveraging-dataset  Exploring E-commerce Trends⭐️⭐️⭐️                 25KB  2024-06-12 18:07:11           1150         30  1.0              
rubenmukherjee/india-2024-election-dataset-all-can

In [ ]:
!kaggle datasets download -d mohammadripan/complaint-sample

Dataset URL: https://www.kaggle.com/datasets/mohammadripan/complaint-sample
License(s): Apache 2.0


In [7]:
!mkdir data
!unzip /content/complaint-sample.zip -d data

Archive:  /content/complaint-sample.zip
  inflating: data/data/complaints_sample.csv  
  inflating: data/word_index.json    


In [ ]:
!pip install tfx

In [2]:
import os
import pandas as pd
import tensorflow as tf
from tfx.components import CsvExampleGen, StatisticsGen, SchemaGen, ExampleValidator, Transform, Trainer, Tuner, Pusher
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext
from tfx.proto import example_gen_pb2
from tfx.v1.components import TunerFnResult
from tfx.dsl.components.common.resolver import Resolver
from tfx.dsl.input_resolution.strategies.latest_blessed_model_strategy import LatestBlessedModelStrategy
from tfx.types import Channel
from tfx.types.standard_artifacts import Model, ModelBlessing
import tensorflow_model_analysis as tfma
from tfx.components import Evaluator
from tensorflow_model_analysis.metrics import specs_from_metrics
from tensorflow_model_analysis import BinarizationOptions
from tfx.proto import trainer_pb2
from tfx.proto import pusher_pb2

import logging
tf.get_logger().setLevel(logging.INFO)

##Set variabel

In [3]:
PIPELINE_NAME = "asyah_majid-pipeline"
SCHEMA_PIPELINE_NAME = "complaint-prediction-model"

PIPELINE_ROOT = os.path.join('pipelines', PIPELINE_NAME)
METADATA_PATH = os.path.join('metadata', PIPELINE_NAME, 'metadata.db')
SERVING_MODEL_DIR = os.path.join('serving_model_dir', PIPELINE_NAME)

##Data Ingestion

In [4]:
# Define the path to your dataset
DATA_ROOT = 'data/data'

# Initialize the TFX interactive context
context = InteractiveContext(pipeline_root=PIPELINE_ROOT)

# 1. ExampleGen
output = example_gen_pb2.Output(split_config=example_gen_pb2.SplitConfig(splits=[
    example_gen_pb2.SplitConfig.Split(name='train', hash_buckets=4),
    example_gen_pb2.SplitConfig.Split(name='eval', hash_buckets=1),
]))
example_gen = CsvExampleGen(input_base=DATA_ROOT, output_config=output)
context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 1
    outputs:
        examples: OutputChannel(artifact_type=Examples, producer_component_id=CsvExampleGen, output_key=examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

##Data Validation

In [5]:
# 2. StatisticsGen
statistics_gen = StatisticsGen(examples=example_gen.outputs['examples'])
context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 2
    outputs:
        statistics: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=StatisticsGen, output_key=statistics, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [6]:
context.show(statistics_gen.outputs['statistics'])

In [7]:
# 3. SchemaGen
schema_gen = SchemaGen(statistics=statistics_gen.outputs['statistics'], infer_feature_shape=True)
context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 3
    outputs:
        schema: OutputChannel(artifact_type=Schema, producer_component_id=SchemaGen, output_key=schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [8]:
context.show(schema_gen.outputs['schema'])

Type  Presence Valency Domain
Feature name                                        
'Consumer_complaint'  BYTES  required              -
'Product'               INT  required              -

In [9]:
# 4. ExampleValidator
example_validator = ExampleValidator(statistics=statistics_gen.outputs['statistics'], schema=schema_gen.outputs['schema'])
context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 4
    outputs:
        anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=ExampleValidator, output_key=anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [ ]:
context.show(example_validator.outputs['anomalies'])

##Data Preprocessing

In [11]:
TRANSFORM_MODULE_FILE = "MyProject_transform.py"

In [12]:
%%writefile {TRANSFORM_MODULE_FILE}

import tensorflow as tf

LABEL_KEY = "Product"
FEATURE_KEY = "Consumer_complaint"

def transformed_name(key):
  return key + '_xf'

def preprocessing_fn(inputs):
  outputs = {}

  outputs[transformed_name(FEATURE_KEY)] = tf.strings.lower(inputs[FEATURE_KEY])

  outputs[transformed_name(LABEL_KEY)] = tf.cast(inputs[LABEL_KEY], tf.int64)

  return outputs

Overwriting MyProject_transform.py


In [14]:
# 5. Transform
transform = Transform(examples=example_gen.outputs['examples'], schema=schema_gen.outputs['schema'], module_file=os.path.abspath(TRANSFORM_MODULE_FILE))
context.run(transform)

ExecutionResult(
    component_id: Transform
    execution_id: 6
    outputs:
        transform_graph: OutputChannel(artifact_type=TransformGraph, producer_component_id=Transform, output_key=transform_graph, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        transformed_examples: OutputChannel(artifact_type=Examples, producer_component_id=Transform, output_key=transformed_examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        updated_analyzer_cache: OutputChannel(artifact_type=TransformCache, producer_component_id=Transform, output_key=updated_analyzer_cache, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=pre_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=pre_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=post_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=post_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=Transform, output_key=post_transform_anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

##Model Development

In [15]:
TUNER_MODULE_FILE = 'tuner_complaint.py'

In [16]:
%%writefile {TUNER_MODULE_FILE}
from kerastuner.engine import base_tuner
import kerastuner as kt
from numpy import dtype
from sympy import factor
from tensorflow import keras
from tensorflow.keras import layers

from typing import NamedTuple, Dict, Text, Any
from tfx.components.trainer.fn_args_utils import FnArgs
import tensorflow as tf
import tensorflow_transform as tft
import numpy as np

LABEL_KEY = "Product"
FEATURE_KEY = "Consumer_complaint"

VOCAB_SIZE = 10000
SEQUENCE_LENGTH = 100
embedding_dim = 16
num_classes = 4

vectorize_layer = layers.TextVectorization(
    standardize="lower_and_strip_punctuation",
    max_tokens=VOCAB_SIZE,
    output_mode='int',
    output_sequence_length=SEQUENCE_LENGTH)

LABEL_KEY = "Product"
FEATURE_KEY = "Consumer_complaint"

def transformed_name(key):
    key = key.replace('-', '_')
    return key + '_xf'

TunerFnResult = NamedTuple('TunerFnResult', [('tuner', base_tuner.BaseTuner),
                                            ('fit_kwargs', Dict[Text,Any])])



def _gzip_reader_fn(filenames):
    return tf.data.TFRecordDataset(filenames, compression_type='GZIP')

def _input_fn(file_pattern,
             tf_transform_output,
             num_epochs=10,
             batch_size=64)->tf.data.Dataset:
    """Get post_tranform feature & create batches of data"""

    # Get post_transform feature spec
    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy())

    # create batches of data
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=_gzip_reader_fn,
        num_epochs=num_epochs,
        label_key = transformed_name(LABEL_KEY))
    return dataset

def model_builder(hp):
    inputs = tf.keras.Input(shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string)
    reshaped_narrative = tf.reshape(inputs, [-1])
    x = vectorize_layer(reshaped_narrative)
    x = layers.Embedding(VOCAB_SIZE, embedding_dim, name="embedding")(x)
    x = layers.GlobalAveragePooling1D()(x)
    # Hyperparameter tuning for the number of hidden layers
    num_hidden_layers = hp.Int('hidden_layers', min_value=1, max_value=5, default=3)

    # Dynamically add hidden layers based on the chosen hyperparameter
    for i in range(num_hidden_layers):
        x = layers.Dense(32, activation='relu')(x)

    outputs = layers.Dense(num_classes, activation='softmax')(x)

    model = tf.keras.Model(inputs=inputs, outputs=outputs)

    model.compile(
        loss='sparse_categorical_crossentropy',
        optimizer=tf.keras.optimizers.Adam(0.01),
        metrics=['accuracy']
    )

    model.summary()
    return model

def tuner_fn(fn_args: FnArgs) -> TunerFnResult:
    tuner = kt.RandomSearch(
        model_builder,
        objective='val_accuracy',
        max_trials=10,
        executions_per_trial=1,
        directory=fn_args.working_dir,
        project_name='kt_random_search'
    )

    # load transform output
    tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

    train_set = _input_fn(fn_args.train_files, tf_transform_output, 10)
    val_set = _input_fn(fn_args.eval_files, tf_transform_output, 10)

    stop_early = tf.keras.callbacks.EarlyStopping(monitor='val_accuracy', mode='max', patience=10)

    vectorize_layer.adapt(
        [j[0].numpy()[0] for j in [
            i[0][transformed_name(FEATURE_KEY)]
                for i in list(train_set)]])


    return TunerFnResult(
        tuner = tuner,
        fit_kwargs={
            "callbacks":[stop_early],
            "x": train_set,
            "validation_data": val_set,
            "steps_per_epoch": fn_args.train_steps,
            "validation_steps": fn_args.eval_steps,
            "epochs": 10
        }
    )

Overwriting tuner_complaint.py


In [17]:
tuner = Tuner(
        module_file=TUNER_MODULE_FILE,
        examples=transform.outputs['transformed_examples'],
        transform_graph=transform.outputs['transform_graph'],
        schema = schema_gen.outputs['schema'],
        train_args=trainer_pb2.TrainArgs(splits=['train'], num_steps=200),
        eval_args=trainer_pb2.EvalArgs(splits=['eval'], num_steps=50)
    )

context.run(tuner)

Trial 5 Complete [00h 00m 34s]
val_accuracy: 0.8728125095367432

Best val_accuracy So Far: 0.8799999952316284
Total elapsed time: 00h 02m 59s
Results summary
Results in pipelines/asyah_majid-pipeline/.temp/7/kt_random_search
Showing 10 best trials
Objective(name="val_accuracy", direction="max")

Trial 01 summary
Hyperparameters:
hidden_layers: 1
Score: 0.8799999952316284

Trial 00 summary
Hyperparameters:
hidden_layers: 2
Score: 0.8771874904632568

Trial 03 summary
Hyperparameters:
hidden_layers: 3
Score: 0.8743749856948853

Trial 04 summary
Hyperparameters:
hidden_layers: 4
Score: 0.8728125095367432

Trial 02 summary
Hyperparameters:
hidden_layers: 5
Score: 0.8712499737739563


ExecutionResult(
    component_id: Tuner
    execution_id: 7
    outputs:
        best_hyperparameters: OutputChannel(artifact_type=HyperParameters, producer_component_id=Tuner, output_key=best_hyperparameters, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        tuner_results: OutputChannel(artifact_type=TunerResults, producer_component_id=Tuner, output_key=tuner_results, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [18]:
TRAINER_MODULE_FILE = 'MyProject_trainer.py'

In [19]:
%%writefile {TRAINER_MODULE_FILE}
import tensorflow as tf
import tensorflow_transform as tft
from tensorflow.keras import layers
import os
import json
from tfx.components.trainer.fn_args_utils import FnArgs

LABEL_KEY = "Product"
FEATURE_KEY = "Consumer_complaint"

def transformed_name(key):
    """Renaming transformed features"""
    return key + "_xf"

def gzip_reader_fn(filenames):
    """Loads compressed data"""
    return tf.data.TFRecordDataset(filenames, compression_type='GZIP')

def input_fn(file_pattern,
             tf_transform_output,
             num_epochs,
             batch_size=64)->tf.data.Dataset:
    """Get post_tranform feature & create batches of data"""

    # Get post_transform feature spec
    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy())

    # create batches of data
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key = transformed_name(LABEL_KEY))
    return dataset

VOCAB_SIZE = 10000
SEQUENCE_LENGTH = 100

vectorize_layer = layers.TextVectorization(
    standardize="lower_and_strip_punctuation",
    max_tokens=VOCAB_SIZE,
    output_mode='int',
    output_sequence_length=SEQUENCE_LENGTH)

embedding_dim = 16
num_classes = 4

def model_builder(hp):
    inputs = tf.keras.Input(shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string)
    reshaped_narrative = tf.reshape(inputs, [-1])
    x = vectorize_layer(reshaped_narrative)
    x = layers.Embedding(VOCAB_SIZE, embedding_dim, name="embedding")(x)
    x = layers.GlobalAveragePooling1D()(x)

    num_hidden_layers = hp.get('hidden_layers') if hp and 'hidden_layers' in hp else 1
    for i in range(num_hidden_layers):
        x = layers.Dense(64, activation='relu')(x)

    outputs = layers.Dense(num_classes, activation='softmax')(x)

    model = tf.keras.Model(inputs=inputs, outputs=outputs)

    model.compile(
        loss='sparse_categorical_crossentropy',
        optimizer=tf.keras.optimizers.Adam(0.01),
        metrics=['accuracy']
    )
    return model

def _get_serve_tf_examples_fn(model, tf_transform_output):
    model.tft_layer = tf_transform_output.transform_features_layer()

    @tf.function
    def serve_tf_examples_fn(serialized_tf_examples):
        feature_spec = tf_transform_output.raw_feature_spec()
        feature_spec.pop(LABEL_KEY)
        parsed_features = tf.io.parse_example(serialized_tf_examples, feature_spec)
        transformed_features = model.tft_layer(parsed_features)
        return model(transformed_features)

    return serve_tf_examples_fn

def run_fn(fn_args: FnArgs) -> None:
    log_dir = os.path.join(os.path.dirname(fn_args.serving_model_dir), 'logs')

    tensorboard_callback = tf.keras.callbacks.TensorBoard(
        log_dir = log_dir, update_freq='batch'
    )

    es = tf.keras.callbacks.EarlyStopping(monitor='val_accuracy', mode='max', verbose=1, patience=10)
    mc = tf.keras.callbacks.ModelCheckpoint(fn_args.serving_model_dir, monitor='val_accuracy', mode='max', verbose=1, save_best_only=True)


    # Load the transform output
    tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

    # Create batches of data
    train_set = input_fn(fn_args.train_files, tf_transform_output, 10)
    val_set = input_fn(fn_args.eval_files, tf_transform_output, 10)
    vectorize_layer.adapt(
        [j[0].numpy()[0] for j in [
            i[0][transformed_name(FEATURE_KEY)]
                for i in list(train_set)]])


    hp = fn_args.hyperparameters.get('values', {}) if fn_args.hyperparameters else {}
    print(f"hp: {hp}")

    # Build the model
    model = model_builder(hp)

    # Train the model
    model.fit(x = train_set,
            validation_data = val_set,
            callbacks = [tensorboard_callback, es, mc],
            steps_per_epoch = 200,
            validation_steps= 50,
            epochs=10)
    signatures = {
        'serving_default':
        _get_serve_tf_examples_fn(model, tf_transform_output).get_concrete_function(
                                    tf.TensorSpec(
                                    shape=[None],
                                    dtype=tf.string,
                                    name='examples'))
    }
    model.save(fn_args.serving_model_dir, save_format='tf', signatures=signatures)

Overwriting MyProject_trainer.py


In [21]:
trainer = Trainer(
    module_file=os.path.abspath(TRAINER_MODULE_FILE),
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    hyperparameters=tuner.outputs['best_hyperparameters'],
    train_args=trainer_pb2.TrainArgs(splits = ['train']),
    eval_args=trainer_pb2.EvalArgs(splits = ['eval']))
context.run(trainer)

ExecutionResult(
    component_id: Trainer
    execution_id: 9
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Trainer, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        model_run: OutputChannel(artifact_type=ModelRun, producer_component_id=Trainer, output_key=model_run, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [23]:
model_resolver = Resolver(
    strategy_class = LatestBlessedModelStrategy,
    model = Channel(type=Model),
    model_blessing = Channel(type=ModelBlessing)
).with_id('Latest_blessed_model_resolver')

context.run(model_resolver)

ExecutionResult(
    component_id: Latest_blessed_model_resolver
    execution_id: 11
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Latest_blessed_model_resolver, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        model_blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Latest_blessed_model_resolver, output_key=model_blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [24]:
eval_config = tfma.EvalConfig(
    model_specs=[
        tfma.ModelSpec(label_key='Product')
    ],
    slicing_specs=[
        tfma.SlicingSpec()
    ],
    metrics_specs=[
        tfma.MetricsSpec(
            metrics=[
                tfma.MetricConfig(class_name="ExampleCount"),
                tfma.MetricConfig(class_name="SparseCategoricalCrossentropy"),
                tfma.MetricConfig(class_name="Precision", config='{"top_k": 1}'),
                tfma.MetricConfig(class_name="Recall", config='{"top_k": 1}'),
                tfma.MetricConfig(class_name="MultiClassConfusionMatrixPlot"),
                tfma.MetricConfig(class_name='SparseCategoricalAccuracy',
                threshold=tfma.MetricThreshold(
                    value_threshold=tfma.GenericValueThreshold(
                        lower_bound={'value':0.5}),
                    change_threshold=tfma.GenericChangeThreshold(
                        direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                        absolute={'value':0.0001})
                    )
            )
            ],
        )
    ]
)

In [25]:
evaluator = Evaluator(
    examples = example_gen.outputs['examples'],
    model = trainer.outputs['model'],
    baseline_model = model_resolver.outputs['model'],
    eval_config = eval_config
)

context.run(evaluator)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


ExecutionResult(
    component_id: Evaluator
    execution_id: 12
    outputs:
        evaluation: OutputChannel(artifact_type=ModelEvaluation, producer_component_id=Evaluator, output_key=evaluation, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Evaluator, output_key=blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [26]:
eval_result = evaluator.outputs['evaluation'].get()[0].uri
tfma_result = tfma.load_eval_result(eval_result)
tfma.view.render_slicing_metrics(tfma_result)
tfma.addons.fairness.view.widget_view.render_fairness_indicator(
    tfma_result
)

##Model Deployment

In [27]:
pusher = Pusher(
model=trainer.outputs['model'],
model_blessing=evaluator.outputs['blessing'],
push_destination=pusher_pb2.PushDestination(
    filesystem=pusher_pb2.PushDestination.Filesystem(
        base_directory=os.path.join('serving_model_dir/complaint-prediction-model')))
)

context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 13
    outputs:
        pushed_model: OutputChannel(artifact_type=PushedModel, producer_component_id=Pusher, output_key=pushed_model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [28]:
!zip -r serving.zip /content/serving_model_dir

  adding: content/serving_model_dir/ (stored 0%)
  adding: content/serving_model_dir/complaint-prediction-model/ (stored 0%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/ (stored 0%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/variables/ (stored 0%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/variables/variables.data-00000-of-00001 (deflated 15%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/variables/variables.index (deflated 56%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/keras_metadata.pb (deflated 84%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/saved_model.pb (deflated 76%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/fingerprint.pb (stored 0%)
  adding: content/serving_model_dir/complaint-prediction-model/1718356350/assets/ (stored 0%)


In [29]:
from google.colab import files
files.download("serving.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [30]:
!zip -r pipelines.zip /content/pipelines

  adding: content/pipelines/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/CsvExampleGen/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/CsvExampleGen/examples/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/CsvExampleGen/examples/1/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/CsvExampleGen/examples/1/Split-train/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/CsvExampleGen/examples/1/Split-train/data_tfrecord-00000-of-00001.gz (deflated 0%)
  adding: content/pipelines/asyah_majid-pipeline/CsvExampleGen/examples/1/Split-eval/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/CsvExampleGen/examples/1/Split-eval/data_tfrecord-00000-of-00001.gz (deflated 0%)
  adding: content/pipelines/asyah_majid-pipeline/Evaluator/ (stored 0%)
  adding: content/pipelines/asyah_majid-pipeline/Evaluator/blessing/ (stored 0%)
  adding: content/pipelines/asyah_ma

In [31]:
from google.colab import files
files.download("pipelines.zip")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>